In [1]:
# Import needed libraries

import pandas as pd
from tqdm.notebook import tqdm
import requests
from bs4 import BeautifulSoup
from newscatcher import Newscatcher
import requests
import re

In [ ]:
# Check supported german news sites

In [2]:
from newscatcher import urls

german_urls = urls(country = 'de', language = 'de')
german_urls

['spiegel.de',
 'welt.de',
 'faz.net',
 'bild.de',
 'focus.de',
 'handelsblatt.com',
 'zdf.de',
 'stern.de',
 'rp-online.de',
 'taz.de',
 'wiwo.de',
 'mdr.de',
 'stuttgarter-zeitung.de',
 'kicker.de',
 'kn-online.de',
 'wz.de']

In [ ]:
# We will remove BILD (tabloid) and kicker (football newspaper)

In [3]:
remove = ['bild.de', 'kicker.de', 'ghacks.net']

In [4]:
german_urls

['spiegel.de',
 'welt.de',
 'faz.net',
 'bild.de',
 'focus.de',
 'handelsblatt.com',
 'zdf.de',
 'stern.de',
 'rp-online.de',
 'taz.de',
 'wiwo.de',
 'mdr.de',
 'stuttgarter-zeitung.de',
 'kicker.de',
 'kn-online.de',
 'wz.de']

In [5]:
german_urls_clean = [url for url in german_urls if url not in remove]

In [6]:
german_urls_clean.extend(['tagesschau.de'])

In [7]:
german_urls_clean

['spiegel.de',
 'welt.de',
 'faz.net',
 'focus.de',
 'handelsblatt.com',
 'zdf.de',
 'stern.de',
 'rp-online.de',
 'taz.de',
 'wiwo.de',
 'mdr.de',
 'stuttgarter-zeitung.de',
 'kn-online.de',
 'wz.de',
 'tagesschau.de']

In [239]:
# Get all the relevant corner data from newspapers
all_news = []

for source in tqdm(german_urls_clean):
    try:
        result = Newscatcher(website = source).get_news()
        articles = result['articles']
        all_news.extend(articles)
    except TypeError:
        continue

  0%|          | 0/15 [00:00<?, ?it/s]

In [240]:
len(all_news)

469

In [241]:
all_news[0]['tags'][0]['term']

'Job & Karriere'

In [242]:
subjects = []

for page in tqdm(range(len(all_news))):
    try:
        subject = all_news[page]['tags'][0]['term']
        subjects.append(subject)
    except KeyError:
        subject = 'no subject stated'
        subjects.append(subject)

  0%|          | 0/469 [00:00<?, ?it/s]

In [243]:
len(subjects)

469

In [244]:
all_news[0]['title']

'Urlaubsgeld: Jeder zweite Tarifbeschäftigte bekommt es - Studie'

In [245]:
titles = []

for page in tqdm(range(len(all_news))):
    title = all_news[page]['title']
    titles.append(title)

  0%|          | 0/469 [00:00<?, ?it/s]

In [246]:
len(titles)

469

In [247]:
all_news[0]['link']

'https://www.spiegel.de/karriere/urlaubsgeld-jeder-zweite-tarifbeschaeftigte-bekommt-es-studie-a-5c22cd75-90b1-400a-bfd7-e3b1248b2c9e#ref=rss'

### Get all the pages that I want to scrape for content

In [248]:
pages = []

for page in tqdm(range(len(all_news))):
    link = all_news[page]['link']
    pages.append(link)

  0%|          | 0/469 [00:00<?, ?it/s]

In [249]:
len(pages)

469

In [250]:
pages[0]

'https://www.spiegel.de/karriere/urlaubsgeld-jeder-zweite-tarifbeschaeftigte-bekommt-es-studie-a-5c22cd75-90b1-400a-bfd7-e3b1248b2c9e#ref=rss'

### Get news content from all the pages

In [251]:
from time import sleep
from random import randint

In [252]:
page_content = []

for i in tqdm(range(len(pages))):
    url = str(pages[i])
    response = requests.get(url)
    page_content.append(response)
    wait_time = randint(1,3)

  0%|          | 0/469 [00:00<?, ?it/s]

In [253]:
page_content[:5]

[<Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>]

In [254]:
paragraphs = []

for page in tqdm(range(len(page_content))):
    paragraph = BeautifulSoup(page_content[page].content, "html.parser")
    paragraphs.append(paragraph)

  0%|          | 0/469 [00:00<?, ?it/s]

In [255]:
def get_content(l):
    contents = []

    for page in tqdm(range(len(l))):
        paragraph = BeautifulSoup(l[page].content, "html.parser")
        contents.append(paragraph)
        return contents
    return content

In [256]:
p_tags = []

for paragraph in tqdm(range(len(paragraphs))):
    tags = paragraphs[paragraph].find_all('p')
    p_tags.append(tags)

  0%|          | 0/469 [00:00<?, ?it/s]

In [257]:
for p in p_tags[0]:
    print(p.get_text())

Strand von Zinnowitz (Archivfoto): Unter anderem dort wird das Urlaubsgeld wieder ausgegeben
Urlaubsspaß in Euro und Cent: Nur knapp die Hälfte der Tarifbeschäftigten in Deutschland (47 Prozent) können in diesen Wochen mit einem Urlaubsgeld rechnen. Laut einer Auswertung des Statistischen Bundesamts fließen bei ihnen im Schnitt 1525 Euro in die Urlaubskasse. Das sind 0,6 Prozent oder neun Euro mehr als im Vorjahr.
Mit 1570 Euro ist die durchschnittliche Zahlung im Westen wesentlich höher als im Osten, wo nur 1104 Euro gezahlt werden. Die Tarifverträge der verschiedenen Branchen sehen sehr unterschiedliche Beträge vor, zwischen 219 Euro bei der Zeitarbeit und 3486 Euro bei Informationsdienstleistern.
Insbesondere im öffentlichen Bereich gibt es sehr selten tariflich vereinbarte Urlaubsgelder, die zudem noch sehr niedrig ausfallen. Am ehesten können Beschäftigte des verarbeitenden Gewerbes und am Bau mit zusätzlichen Zahlungen bis zu einem vollen Monatsgehalt rechnen.
Der Anteil von 47 P

In [258]:
[i for i in p_tags]

[[<p>Strand von Zinnowitz (Archivfoto): Unter anderem dort wird das Urlaubsgeld wieder ausgegeben</p>,
  <p>Urlaubsspaß in Euro und Cent: Nur knapp die Hälfte der Tarifbeschäftigten in Deutschland (47 Prozent) können in diesen Wochen mit einem Urlaubsgeld rechnen. Laut einer Auswertung des Statistischen Bundesamts fließen bei ihnen im Schnitt 1525 Euro in die Urlaubskasse. Das sind 0,6 Prozent oder neun Euro mehr als im Vorjahr.</p>,
  <p>Mit 1570 Euro ist die durchschnittliche Zahlung im Westen wesentlich höher als im Osten, wo nur 1104 Euro gezahlt werden. Die Tarifverträge der verschiedenen Branchen sehen sehr unterschiedliche Beträge vor, zwischen 219 Euro bei der Zeitarbeit und 3486 Euro bei Informationsdienstleistern.</p>,
  <p>Insbesondere im öffentlichen Bereich gibt es sehr selten tariflich vereinbarte Urlaubsgelder, die zudem noch sehr niedrig ausfallen. Am ehesten können Beschäftigte des verarbeitenden Gewerbes und am Bau mit zusätzlichen Zahlungen bis zu einem vollen Monats

In [259]:
final_content = ["\n".join(p.get_text() for p in i) for i in p_tags]

In [260]:
len(final_content)

469

In [261]:
final_content[459]

'\n                    Stand: 27.07.2021 00:09 Uhr\n                \n\nTesla-Chef Musk hat es mal wieder allen Skeptikern gezeigt: Im abgelaufenen Quartal lieferte der US-Konzern so viele E-Autos aus wie nie und verdiente erstmals mehr als eine Milliarde Dollar.\n\n\n        Vor vier Wochen hat der "Technoking" seinen 50. Geburtstag gefeiert. Nun macht sich Tesla-Chef Elon Musk selbst sein schönstes Geschenk: das beste Quartalsergebnis der Geschichte. Trotz des weltweiten Chipmangels und der Rohstoff-Engpässe hat der Elektroauto-Pionier im Zeitraum von April bis Ende Juli den Umsatz um satte 87 Prozent auf gut 12 Milliarden Dollar gesteigert. Der Gewinn verzehnfachte sich gar auf 1,1 Milliarden Dollar. Es war der erste Milliardengewinn in einem Quartal.\n    \n\n        Auch bei der Produktion und der Auslieferung erreichte Tesla neue Rekorde. Mit über 201.000 Fahrzeugen lieferte der Tech-Konzern so viele Stromer aus wie noch nie in einem Vierteljahr. Insgesamt produzierte Tesla 206.4

### Create the data frame

In [47]:
real_ger_news = pd.DataFrame(titles, columns=['titles'])

In [48]:
real_ger_news.head()

titles
0  Windräder in Deutschland: Ausbau reicht nicht ...
1  Anerkennung des Missbrauchs: Knapp 19.000 früh...
2  Joe Biden will Steuerschlupfloch für Tote stopfen
3  Vatikan: Kardinal Angelo Becciu steht wegen Lu...
4  Olympia 2021: Naomi Osaka verliert im Tennis b...

In [49]:
real_ger_news['content'] = final_content

In [50]:
real_ger_news['subject'] = subject

In [51]:
real_ger_news['label'] = 'True'

In [52]:
real_ger_news.head()

titles  \
0  Windräder in Deutschland: Ausbau reicht nicht ...   
1  Anerkennung des Missbrauchs: Knapp 19.000 früh...   
2  Joe Biden will Steuerschlupfloch für Tote stopfen   
3  Vatikan: Kardinal Angelo Becciu steht wegen Lu...   
4  Olympia 2021: Naomi Osaka verliert im Tennis b...   

                                             content            subject label  
0  Windräder in Brandenburg\nDie Zahlen klingen a...  no subject stated  True  
1  Kinderschaukel (Symbolbild)\nDie genaue Zahl d...  no subject stated  True  
2  US-Präsident Joe Biden\nLEAH MILLIS / REUTERS\...  no subject stated  True  
3  Kardinal Angelo Becciu (2020)\nErstmals muss s...  no subject stated  True  
4  Naomi Osaka scheidet in Tokio früh aus dem Ten...  no subject stated  True

In [53]:
real_ger_news['content'] = real_ger_news['content'].replace(r'\n',' ', regex=True)

In [54]:
real_ger_news.head(5)

titles  \
0  Windräder in Deutschland: Ausbau reicht nicht ...   
1  Anerkennung des Missbrauchs: Knapp 19.000 früh...   
2  Joe Biden will Steuerschlupfloch für Tote stopfen   
3  Vatikan: Kardinal Angelo Becciu steht wegen Lu...   
4  Olympia 2021: Naomi Osaka verliert im Tennis b...   

                                             content            subject label  
0  Windräder in Brandenburg Die Zahlen klingen au...  no subject stated  True  
1  Kinderschaukel (Symbolbild) Die genaue Zahl de...  no subject stated  True  
2  US-Präsident Joe Biden LEAH MILLIS / REUTERS  ...  no subject stated  True  
3  Kardinal Angelo Becciu (2020) Erstmals muss si...  no subject stated  True  
4  Naomi Osaka scheidet in Tokio früh aus dem Ten...  no subject stated  True

In [262]:
real_ger_news.to_csv('real_ger_news_3.csv', index = False)

In [263]:
ls

German News Scrapping.ipynb  real_ger_news_1
GermanFakeNC.json            real_ger_news_1.csv
fake_ger_news_1.csv          real_ger_news_2.csv
fake_ger_news_2.csv          real_ger_news_3.csv


In [43]:
pd.read_csv('real_ger_news_1.csv').head()

titles  \
0  Corona-Pandemie: Christine Lambrecht (SPD) spr...   
1  Unwetter in Sachsen, Bayern und Berlin: 67-Jäh...   
2  Olympia 2021: Triathlon der Männer beginnt mit...   
3  Galeria Karstadt Kaufhof kündigt Neustart mit ...   
4  Olympia heute – Tag drei: Was in der Nacht ges...   

                                             content            subject  label  
0  Bundesinnenminister Horst Seehofer (CSU), Bund...  no subject stated   True  
1  Überflutete Straße im bayerischen Penzberg Wäh...  no subject stated   True  
2  Panne bei Olympia: Ein Teil der Triathleten wu...  no subject stated   True  
3  Filiale von Galeria Kaufhof in Köln Reihenweis...  no subject stated   True  
4  Sideris Tasiadis peilt eine Medaille an Ein Fe...  no subject stated   True

### Get Fake News from JSON file

In [280]:
import json

In [282]:
with open('GermanFakeNC.json') as json_file:
    data = json.load(json_file)

In [298]:
data[2].keys()

dict_keys(['Date', 'URL', 'False_Statement_1_Location', 'False_Statement_1_Index', 'False_Statement_2_Location', 'False_Statement_2_Index', 'False_Statement_3_Location', 'False_Statement_3_Index', 'Ratio_of_Fake_Statements', 'Overall_Rating'])

In [294]:
data[2]['URL']

'http://blauerbote.com/2017/06/02/angela-merkel-laesst-rock-am-ring-abbrechen/'

In [295]:
fake_urls = []

for entry in tqdm(range(len(data))):
    fake_urls.append(data[entry]['URL'])

  0%|          | 0/490 [00:00<?, ?it/s]

In [296]:
fake_urls

['https://schluesselkindblog.com/2017/08/30/prozess-beginnt-mord-an-heidelberger-studentin/',
 'http://blauerbote.com/2017/12/18/bild-journalist-julian-roepcke-und-seine-nazifreunde/',
 'http://blauerbote.com/2017/06/02/angela-merkel-laesst-rock-am-ring-abbrechen/',
 'http://smopo.ch/deutschlands-neonazis-waehlen-den-untergang/',
 'http://www.truth24.net/gruppenvergewaltigung-sex-jihadisten-vergewaltigen-junge-deutsche-auf-heimweg/',
 'http://www.rapefugees.net/ozapft-is-tuerke-versucht-koreanerin-auf-die-wiesn-zu-vergewaltigen-oktoberfest-startet-dreckig-muenchen/',
 'https://blog.halle-leaks.de/dresden-wieder-kind-durch-fluechtling-brutal-vergewaltigt-wie-lange-noch/',
 'https://www.unzensuriert.at/content/0026189-Katalonien-100-Tage-Diktatur-des-spanischen-Zentralstaats',
 'http://www.guidograndt.de/2018/01/22/kollegenbeitrag-waehler-verraeter-spd/',
 'https://de.sott.net/article/31971-Umfrage-92-der-Ukrainer-wollen-russischen-Fuhrer-zuruck-Schnauze-voll-von-Poroschenko',
 'http://i

In [301]:
# Get all fake news
fake_page_content = []

for i in tqdm(range(len(fake_urls))):
    try:
        url = str(fake_urls[i])
        response = requests.get(url)
        fake_page_content.append(response)
        wait_time = randint(1,3)
    except:
        continue

  0%|          | 0/490 [00:00<?, ?it/s]

In [304]:
fake_page_content[5:]

[<Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [403]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [406]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [200]>,
 <Response [404]>,
 <Response [200]>,
 <Response [200]>,
 <Response [

In [308]:
fake_page_content = [page for page in fake_page_content if page.status_code == 200]

In [309]:
len(fake_page_content)

328

In [310]:
fake_content = []

for page in tqdm(range(len(fake_page_content))):
    content = BeautifulSoup(fake_page_content[page].content, "html.parser")
    fake_content.append(content)

  0%|          | 0/328 [00:00<?, ?it/s]

In [390]:
fake_p_tags = []

for paragraph in tqdm(range(len(fake_content))):
    tags = fake_content[paragraph].find_all('p')
    fake_p_tags.append(tags)

  0%|          | 0/328 [00:00<?, ?it/s]

In [391]:
fake_p_tags

[[],
 [<p class="site-title"><a href="http://blauerbote.com/" rel="home">Blauer Bote Magazin – Wissenschaft statt Propaganda</a></p>,
  <p>Es ist schon ein (Haken-) Kreuz mit der Bildzeitung… BILD-Reporter und „Russland-Spezialist“ Julian Röpcke – laut BILD-Cheffe Julian Reichelt ein ganz ausgezeichneter Journalist – mit seinen Kumpels vom rechtsextremen ukrainischen Asow-Bataillon, welches sich sein Logo von der Waffen-SS aus dem Dritten Reich geborgt hat. Featuring Mikael Skillt (Schwedischer Neonazi und Scharfschütze) und „Thomas C. Theiner“ („We all know Hitler’s only mistake was to not have killed enough Russians.“): <span id="more-13150"></span></p>,
  <p><a href="http://blauerbote.com/wp-content/uploads/2017/12/bild_nazis_julian_roepcke_asow_bataillon_ss.png"><img alt="" class="alignnone size-full wp-image-13151" height="646" sizes="(max-width: 935px) 100vw, 935px" src="http://blauerbote.com/wp-content/uploads/2017/12/bild_nazis_julian_roepcke_asow_bataillon_ss.png" srcset="http

In [393]:
final_fake_content = ["\n".join(p.get_text() for p in i) for i in fake_p_tags]

In [395]:
len(final_fake_content)

328

In [411]:
fake_titles = []

for title in tqdm(range(len(fake_content))):
    tags = fake_content[title].find_all('h1')
    fake_titles.append(tags)

  0%|          | 0/328 [00:00<?, ?it/s]

In [412]:
fake_titles

[[],
 [<h1 class="entry-title">BILD-Journalist Julian Röpcke und seine Nazifreunde</h1>],
 [<h1 class="entry-title">Angela Merkel läßt Rock am Ring abbrechen</h1>],
 [<h1 class="post-title entry-title">
  			Gruppenvergewaltigung: Sex Jihadisten vergewaltigen junge Deutsche auf Heimweg			        </h1>,
  <h1>Bad Soden / Hofheim. Beim Herumvagabundieren überfielen die beiden Araber einfach eine junge Frau, sie wollte nur nach Hause</h1>],
 [<h1 class="entry-title">Ozapft Is! Türke versucht Koreanerin auf die Wiesn zu vergewaltigen – Oktoberfest startet dreckig | München</h1>,
  <h1>Bereits der erste Tag startet wieder mit einer versuchten Vergewaltigung durch einen Moslem, die Tagesschau berichtet es sei alles friedlich gestartet</h1>],
 [],
 [],
 [<h1 class="site-title"> <a href="http://www.guidograndt.de/" rel="home">GUIDO GRANDT </a></h1>,
  <h1 class="title single"> <a title="Permalink zu: KOLLEGENBEITRAG: “Wähler-Verräter SPD?!”">
                    KOLLEGENBEITRAG: “Wähler-Verrät

In [423]:
final_fake_titles = ["\n".join(p.get_text() for p in i) for i in fake_titles]

In [431]:
final_fake_titles[325]

''

In [415]:
len(final_fake_titles)

328

In [424]:
fake_ger_news = pd.DataFrame(final_fake_titles, columns=['titles'])

In [425]:
fake_ger_news['content'] = final_fake_content

In [428]:
fake_ger_news['label'] = 'False'

In [436]:
fake_ger_news['content'] = fake_ger_news['content'].replace(r'\n',' ', regex=True)

<ipython-input-436-2641da548fba>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fake_ger_news['content'] = fake_ger_news['content'].replace(r'\n',' ', regex=True)


In [437]:
fake_ger_news['content'] = fake_ger_news['content'].replace(r'\t',' ', regex=True)

<ipython-input-437-8b4517e75288>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fake_ger_news['content'] = fake_ger_news['content'].replace(r'\t',' ', regex=True)


In [441]:
fake_ger_news['titles'] = fake_ger_news['titles'].replace(r'\n',' ', regex=True)

<ipython-input-441-e6bf6d659494>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fake_ger_news['titles'] = fake_ger_news['titles'].replace(r'\n',' ', regex=True)


In [442]:
fake_ger_news['titles'] = fake_ger_news['titles'].replace(r'\t',' ', regex=True)

<ipython-input-442-ee8bfae33cff>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fake_ger_news['titles'] = fake_ger_news['titles'].replace(r'\t',' ', regex=True)


In [443]:
fake_ger_news['titles'] = fake_ger_news['titles'].replace(r'\r',' ', regex=True)

<ipython-input-443-3e8c6ab2f2de>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fake_ger_news['titles'] = fake_ger_news['titles'].replace(r'\r',' ', regex=True)


In [444]:
fake_ger_news

titles  \
1    BILD-Journalist Julian Röpcke und seine Nazifr...   
2            Angela Merkel läßt Rock am Ring abbrechen   
3         Gruppenvergewaltigung: Sex Jihadisten ver...   
4    Ozapft Is! Türke versucht Koreanerin auf die W...   
7     GUIDO GRANDT                       KOLLEGENBE...   
..                                                 ...   
320       Mehrere Sexattacken: Armutsasylanten über...   
322   GUIDO GRANDT                       “SIE KOMME...   
323   GUIDO GRANDT                       AMTLICH: D...   
324  Sex-Dschihad in Essen: 200 „Flüchtlinge“ stürm...   
327   Kindesmissbrauch in 108 Fällen: Pädophiler Pr...   

                                               content  label  
1    Blauer Bote Magazin – Wissenschaft statt Propa...  False  
2    Blauer Bote Magazin – Wissenschaft statt Propa...  False  
3      Suchen  « Er wollte sie im Fluss ertränken: ...  False  
4     Rapefugees.net Vergewaltigungen melden ungesc...  False  
7    Publizist, Autor & investigativer Journalist S...  False  
..                                                 ...    ...  
320    Suchen  « 572 Fälle von Genitalverstümmelung...  False  
322  Publizist, Autor & investigativer Journalist  ...  False  
323  Publizist, Autor & investigativer Journalist  ...  False  
324  Merkels “Fachkräfte” haben erneut zugeschlagen...  False  
327   Philipos Moustaki   Redakteur Philipos Mousta...  False  

[220 rows x 3 columns]

In [445]:
fake_ger_news.to_csv('fake_ger_news_1.csv', index = False)

In [446]:
ls

German News Scrapping.ipynb  real_ger_news_1
GermanFakeNC.json            real_ger_news_1.csv
fake_ger_news_1.csv


### Scrape individual fake news websites to increase sample size

In [57]:
# We will be able to repeat this for every month, since the website has an acceptable structure

url = 'http://blauerbote.com/2021/07/'

In [58]:
response=requests.get(url)
response.status_code

200

In [59]:
bbote = BeautifulSoup(response.content, "html.parser")

In [63]:
print(bbote.prettify())

<!DOCTYPE html>
<html lang="de-DE">
 <head>
  <meta charset="utf-8"/>
  <meta content="width=device-width, initial-scale=1" name="viewport"/>
  <link href="http://gmpg.org/xfn/11" rel="profile"/>
  <link href="http://blauerbote.com/xmlrpc.php" rel="pingback"/>
  <title>
   Juli 2021 – Blauer Bote Magazin – Wissenschaft statt Propaganda
  </title>
  <link href="//fonts.googleapis.com" rel="dns-prefetch">
   <link href="//s.w.org" rel="dns-prefetch">
    <link href="http://blauerbote.com/feed/" rel="alternate" title="Blauer Bote Magazin - Wissenschaft statt Propaganda » Feed" type="application/rss+xml"/>
    <link href="http://blauerbote.com/comments/feed/" rel="alternate" title="Blauer Bote Magazin - Wissenschaft statt Propaganda » Kommentar-Feed" type="application/rss+xml"/>
    <script type="text/javascript">
     window._wpemojiSettings = {"baseUrl":"https:\/\/s.w.org\/images\/core\/emoji\/2.3\/72x72\/","ext":".png","svgUrl":"https:\/\/s.w.org\/images\/core\/emoji\/2.3\/svg\/","svgEx

In [80]:
# create the url string for the page search
# we don't really need a complex iterations variable, since the url-structure is very simple

iterations = range(2,6,1)

july = ['http://blauerbote.com/2021/07']

for i in iterations:
        start_at =str(i)
        url='http://blauerbote.com/2021/07/page/' + start_at + '/'
        july.append(url)

In [81]:
july

['http://blauerbote.com/2021/07',
 'http://blauerbote.com/2021/07/page/2/',
 'http://blauerbote.com/2021/07/page/3/',
 'http://blauerbote.com/2021/07/page/4/',
 'http://blauerbote.com/2021/07/page/5/']

In [91]:
def get_pages(l):
    for i in tqdm(iterations):
        start_at ='/page/' + str(i) + '/'
        url= l[0] + start_at
        l.append(url)
    return l

In [88]:
june = ['http://blauerbote.com/2021/06/']
may = ['http://blauerbote.com/2021/05/']
april = ['http://blauerbote.com/2021/04/']
march = ['http://blauerbote.com/2021/03/']
february = ['http://blauerbote.com/2021/02/']
january = ['http://blauerbote.com/2021/01/']
december = ['http://blauerbote.com/2020/12/']
november = ['http://blauerbote.com/2020/11/']

In [92]:
get_pages(june)
get_pages(may)
get_pages(april)
get_pages(march)
get_pages(february)
get_pages(january)
get_pages(december)
get_pages(november)

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

['http://blauerbote.com/2020/11/',
 'http://blauerbote.com/2020/11//page/2/',
 'http://blauerbote.com/2020/11//page/3/',
 'http://blauerbote.com/2020/11//page/4/',
 'http://blauerbote.com/2020/11//page/5/']

In [93]:
import itertools

In [94]:
blau_links = itertools.chain(july, june, may, april, march, february, january, december, november)

In [97]:
blau_links = list(blau_links)

In [98]:
blau_links

['http://blauerbote.com/2021/07',
 'http://blauerbote.com/2021/07/page/2/',
 'http://blauerbote.com/2021/07/page/3/',
 'http://blauerbote.com/2021/07/page/4/',
 'http://blauerbote.com/2021/07/page/5/',
 'http://blauerbote.com/2021/06/',
 'http://blauerbote.com/2021/06//page/2/',
 'http://blauerbote.com/2021/06//page/3/',
 'http://blauerbote.com/2021/06//page/4/',
 'http://blauerbote.com/2021/06//page/5/',
 'http://blauerbote.com/2021/06//page/2/',
 'http://blauerbote.com/2021/06//page/3/',
 'http://blauerbote.com/2021/06//page/4/',
 'http://blauerbote.com/2021/06//page/5/',
 'http://blauerbote.com/2021/05/',
 'http://blauerbote.com/2021/05//page/2/',
 'http://blauerbote.com/2021/05//page/3/',
 'http://blauerbote.com/2021/05//page/4/',
 'http://blauerbote.com/2021/05//page/5/',
 'http://blauerbote.com/2021/05//page/2/',
 'http://blauerbote.com/2021/05//page/3/',
 'http://blauerbote.com/2021/05//page/4/',
 'http://blauerbote.com/2021/05//page/5/',
 'http://blauerbote.com/2021/04/',
 'htt

In [99]:
pages =[]

for url in tqdm(blau_links):
    response = requests.get(url)
    print("status=" + str(response.status_code))
    pages.append(response) 
    wait_time=randint(1,3)
    sleep(wait_time)

  0%|          | 0/53 [00:00<?, ?it/s]

status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=404
status=200
status=200
status=200
status=404
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=404
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200
status=200


In [100]:
pages = [page for page in pages if page.status_code == 200]

In [184]:
def page_requests(l):
    
    pages_raw =[]

    for url in tqdm(range(len(l))):
        response = requests.get(url)
        print("status=" + str(response.status_code))
        pages.append(response) 
        wait_time= 0.1
        sleep(wait_time)

In [101]:
len(pages)

50

In [103]:
page1 = BeautifulSoup(pages[0].content,"html.parser")

In [119]:
page1.select('a.more-link')[0]['href']

'http://blauerbote.com/2021/07/26/the-recommended-genetic-manipulation-of-humans/'

In [127]:
content = []

for page in tqdm(range(len(pages))):
    contents = BeautifulSoup(pages[page].content,"html.parser")
    content.append(contents)

  0%|          | 0/50 [00:00<?, ?it/s]

In [140]:
hrefs = []

for link in content:
    raw_link = link.select('a.more-link')
    for i in range(len(raw_link)):
        href = raw_link[i]['href']
        hrefs.append(href)

In [190]:
hrefs[0]

'http://blauerbote.com/2021/07/26/the-recommended-genetic-manipulation-of-humans/'

In [192]:
pages_raw =[]

for url in tqdm(hrefs):
    response = requests.get(url)
    pages_raw.append(response) 
    wait_time= 0.1
    sleep(wait_time)

  0%|          | 0/1128 [00:00<?, ?it/s]

In [194]:
len(pages_raw)

1128

In [204]:
fake_paragaphs = get_content(pages_raw)

  0%|          | 0/1128 [00:00<?, ?it/s]

In [206]:
fake_contents = []

for page in tqdm(range(len(pages_raw))):
    paragraph = BeautifulSoup(pages_raw[page].content, "html.parser")
    fake_contents.append(paragraph)

  0%|          | 0/1128 [00:00<?, ?it/s]

In [207]:
len(fake_contents)

1128

In [ ]:
# header > h1 (header)
# div.entry-content.clearfix (text)

In [216]:
fake_contents[0].select('header > h1')[0].get_text()

'The recommended genetic manipulation of humans'

In [220]:
fake_contents[0].select('div.entry-content.clearfix')[0].get_text()

'\nThe WHO has published official recommendations on DNA manipulation of humans.\nThose who warned that Corona „vaccinations“ were the first step towards the genetic manipulation of humans faced harsh attacks from quality media, politicians and activists who denied this and ridiculed the corresponding fears. But all that is now moot: on 12 July 2021, the WHO itself let the cat out of the bag and published recommendations – available to everyone on the WHO website – on the genetic manipulation of humans „to promote public health“ (1).\n\nThe World Health Organisation, about which one could read in the media before the Corona crisis sentences such as „The WHO is itself on the Gates Foundation’s money drip“, writes in its news article „WHO issues new recommendations on human genome editing for the promotion of public health“ on the modification or manipulation of the human genome (1-3):\n„Two new companion\xa0reports\xa0released today by the World Health Organization (WHO) provide the fir

In [225]:
bbl_fake_titles = []
bbl_fake_content = []

for article in tqdm(range(len(fake_contents))):
    title = fake_contents[article].select('header > h1')[0].get_text()
    content = fake_contents[article].select('div.entry-content.clearfix')[0].get_text()
    bbl_fake_titles.append(title)
    bbl_fake_content.append(content)

  0%|          | 0/1128 [00:00<?, ?it/s]

In [226]:
print(len(bbl_fake_titles))
print(len(bbl_fake_content))

1128
1128


In [227]:
fake_bbl_news = pd.DataFrame(bbl_fake_titles, columns=['titles'])

In [229]:
fake_bbl_news['content'] = bbl_fake_content

In [231]:
fake_bbl_news['label'] = 'False'

In [234]:
fake_bbl_news.head()

titles  \
0     The recommended genetic manipulation of humans   
1  Zensur: Google-Suche zeigt kenfm.de nicht mehr an   
2  Professor Krause: „Labordaten allein sollten n...   
3  Deutschland boykottiert Anti-Rassismus-Konfere...   
4  Tatsächlich ist nicht das System dumm und fade...   

                                             content  label  
0  \nThe WHO has published official recommendatio...  False  
1  \nWer „kenfm“ oder „kenfm.de“ in die Google-Su...  False  
2  \n„Labordaten allein sollten nicht unser Hande...  False  
3  \nDeutschland boykottiert Anti-Rassismus-Konfe...  False  
4  \n\nTherapien: Tatsächlich ist nicht das Syste...  False

In [235]:
fake_bbl_news['content'] = fake_bbl_news['content'].replace(r'\n',' ', regex=True)

In [236]:
fake_bbl_news.head()

titles  \
0     The recommended genetic manipulation of humans   
1  Zensur: Google-Suche zeigt kenfm.de nicht mehr an   
2  Professor Krause: „Labordaten allein sollten n...   
3  Deutschland boykottiert Anti-Rassismus-Konfere...   
4  Tatsächlich ist nicht das System dumm und fade...   

                                             content  label  
0   The WHO has published official recommendation...  False  
1   Wer „kenfm“ oder „kenfm.de“ in die Google-Suc...  False  
2   „Labordaten allein sollten nicht unser Handel...  False  
3   Deutschland boykottiert Anti-Rassismus-Konfer...  False  
4    Therapien: Tatsächlich ist nicht das System ...  False

In [237]:
fake_bbl_news.to_csv('fake_ger_news_2.csv', index = False)

In [264]:
ls

German News Scrapping.ipynb  real_ger_news_1
GermanFakeNC.json            real_ger_news_1.csv
fake_ger_news_1.csv          real_ger_news_2.csv
fake_ger_news_2.csv          real_ger_news_3.csv
